In [1]:
import os
import glob
import pickle
import warnings

warnings.filterwarnings("ignore")
import matplotlib
import matplotlib.pyplot as plt
from datetime import datetime
from Toolshed import (
    Download,
    Toolbox,
    VegetationLine,
    Plotting,
    PlottingSeaborn,
    Transects,
)
import ee
import geopandas as gpd
import geemap
from tqdm.auto import tqdm
from shapely.geometry import MultiLineString

service_account = 'service-account@iron-dynamics-294100.iam.gserviceaccount.com'
credentials = ee.ServiceAccountCredentials(service_account, '../CoastSat/.private-key.json')
ee.Initialize(credentials)
#ee.Authenticate()  # should only need to be run the first time after installation

In [2]:
poly = gpd.read_file("../CoastSat/polygons.geojson")
poly = poly[poly.id.str.startswith("nzd")].to_crs(2193)
mhwl = gpd.read_file("lds-nz-coastline-mean-high-water-GPKG.zip!nz-coastline-mean-high-water.gpkg")
sitename = "nzd0357"
bbox = poly[poly.id == sitename].geometry.iloc[0]
clipped_mhwl = mhwl.clip(bbox)
display(clipped_mhwl)
m = clipped_mhwl.explore("length", tiles="ESRI.WorldImagery")
clipped_mhwl.buffer(80).explore(m=m)
m

id coast_category  publish_date               source  scale length  \
6879    5589           None          2017  Topo Map Sheet BR29  50000    975   
16602  16241    stony shore          2017  Topo Map Sheet BR29  50000   1561   
16624  16264    stony shore          2017  Topo Map Sheet BR29  50000   2231   
1630     153           None          2017  Topo Map Sheet BR29  50000  38105   
16626  16266    stony shore          2017  Topo Map Sheet BR29  50000   5776   
595    10729           None          2017  Topo Map Sheet BR29  50000   2802   
15754  15282    steep coast          2017  Topo Map Sheet BR29  50000   3833   

                                                geometry  
6879   LINESTRING (1692324.06 5401467.928, 1692341.55...  
16602  LINESTRING (1688646.228 5405324.776, 1688647.8...  
16624  MULTILINESTRING ((1691984.151 5401430.53, 1691...  
1630   MULTILINESTRING ((1688654.246 5405249.255, 168...  
16626  LINESTRING (1688689.768 5405184.547, 1688689.7...  
595    LINESTRING (1692871.472 5401506.517, 1692871.4...  
15754  LINESTRING (1694761.493 5399489.025, 1694761.5...

In [4]:
NZCCD = gpd.read_file(
    "https://github.com/UoA-eResearch/retrolens/raw/refs/heads/main/Data%20for%20testing/NZCCDv1.shp"
)
NZCCD

Region              Site Digitiser  Scale           Notes Source  \
0        Auckland  KarekareBethells        MW   2000             tod     RL   
1        Auckland  KarekareBethells        MW   2000             tod     RL   
2        Auckland  KarekareBethells        MW   2000  tod (landward)     RL   
3        Auckland  KarekareBethells        MW   2000             tod     RL   
4        Auckland  KarekareBethells        MW   2000             tod     RL   
...           ...               ...       ...    ...             ...    ...   
19661  West Coast     WoodpeckerBay        MD   1000         EdgeVeg     RL   
19662       Otago            Oamaru        TK   1500    Top of cliff    Max   
19663       Otago            Oamaru        TK   1500    Top of cliff    Max   
19664       Otago            Oamaru        TK   1500    Top of cliff    Max   
19665       Otago            Oamaru        TK   1509    Top of cliff    Max   

       CPS  Proxy  Photoscale  Georef_ER  Pixel_Er  Total_UNCY      USDate  \
0        4      1       40000       5.03  1.416425    5.620681  01/02/2004   
1        4      1       40000       5.03  1.416425    5.620681  01/02/2004   
2        4      1       40000       5.03  1.416425    5.620681  01/02/2004   
3        3      1       40000       5.03  1.416425    5.314890  01/02/2004   
4        4      1       40000       5.03  1.416425    5.620681  01/02/2004   
...    ...    ...         ...        ...       ...         ...         ...   
19661    2      1       18800       4.00  0.630693    3.736680  11/18/1948   
19662    3      2           0       2.02  0.412236    2.278429  04/04/2018   
19663    3      2           0       2.02  0.412236    2.278429  04/04/2018   
19664    3      2           0       2.02  0.412236    2.278429  04/04/2018   
19665    3      2           0       2.02  0.412236    2.278429  04/04/2018   

       SHLength       Date       ID  \
0      1.265403 2004-01-02      0.0   
1      0.307010 2004-01-02      1.0   
2      0.255243 2004-01-02      2.0   
3      1.107251 2004-01-02      3.0   
4      0.770375 2004-01-02      4.0   
...         ...        ...      ...   
19661  1.191368 1948-11-18  19661.0   
19662  0.650952 2018-04-04  19662.0   
19663  0.179434 2018-04-04  19663.0   
19664  0.174825 2018-04-04  19664.0   
19665  0.699719 2018-04-04  19665.0   

                                                geometry  
0      LINESTRING Z (1728907.5 5916213.248 0, 1728868...  
1      LINESTRING Z (1729067.838 5914779.733 0, 17290...  
2      LINESTRING Z (1729647.881 5911983.994 0, 17296...  
3      MULTILINESTRING Z ((1728131.079 5917218.888 0,...  
4      MULTILINESTRING Z ((1729643.228 5912906.682 0,...  
...                                                  ...  
19661  LINESTRING Z (1467237.671 5348414.193 0, 14672...  
19662  LINESTRING Z (1444386.944 5008247.367 0, 14443...  
19663  LINESTRING Z (1444860.629 5008686.925 0, 14448...  
19664  LINESTRING Z (1444996.286 5008822.252 0, 14450...  
19665  LINESTRING Z (1445121.287 5008941.631 0, 14451...  

[19666 rows x 17 columns]

In [4]:
NZCCD[NZCCD.Region == "Auckland"].explore()

In [13]:
# Define AOI using coordinates of a rectangle
# The points represent the corners of a bounding box that go around your site
# sitename = "nzd0187"

# Date range

dates = ["1900-01-01", "2030-01-01"]

# Satellite missions
# Input a list of containing any/all of 'L5', 'L7', 'L8', 'L9', 'S2', 'PSScene4Band'
# L5: 1984-2013; L7: 1999-2017 (SLC error from 2003); L8: 2013-present; S2: 2014-present; L9: 2021-present
sat_list = ["L5", "L7", "L8", "L9"]

# Cloud threshold for screening out cloudy imagery (0.5 or 50% recommended)
cloud_thresh = 0.5

# Extract shoreline (wet-dry boundary) as well as veg edge
wetdry = False

# Reference shoreline/veg line shapefile name (should be stored in a folder called referenceLines in Data)
# Line should be ONE CONTINUOUS linestring along the shore, stored as a shapefile in WGS84 coord system
referenceLineShp = sitename + ".geojson"
# Maximum amount in metres by which to buffer the reference line for capturing veg edges within
max_dist_ref = 200

In [4]:
sitename

'nzd0357'

### Set Up Site Directory
Make a series of directories for the new sitename.

In [6]:
# Directory where the data will be stored
!rm -rf test/{sitename}/
filepath = Toolbox.CreateFileStructure(sitename, sat_list)
filepath

'/mnt/COASTGUARD/Data'

### Reference Shore Option 1: Define AOI from the bounding box of the <font color='red'>reference shoreline shapefile</font>
You shouldn't need to change anything here; the `referenceLineShp` comes from the <font color='red'>User requirements</font> cell

In [7]:
# Return AOI from reference line bounding box and save AOI folium map HTML in sitename directory
referenceLinePath = os.path.join(filepath, "referenceLines", referenceLineShp)
referenceLineDF = gpd.read_file(referenceLinePath)
polygon, point, lonmin, lonmax, latmin, latmax = Toolbox.AOIfromLine(
    referenceLinePath, max_dist_ref, sitename
)

# It's recommended to convert the polygon to the smallest rectangle (sides parallel to coordinate axes)
polygon = Toolbox.smallest_rectangle(polygon)

### Compile Input Settings for Gathering Imagery

In [14]:
if len(dates) > 2:
    daterange = "no"
else:
    daterange = "yes"
years = list(
    Toolbox.daterange(
        datetime.strptime(dates[0], "%Y-%m-%d"),
        datetime.strptime(dates[-1], "%Y-%m-%d"),
    )
)

# Put all the inputs into a dictionary
inputs = {
    "polygon": polygon,
    "dates": dates,
    "daterange": daterange,
    "sat_list": sat_list,
    "sitename": sitename,
    "filepath": filepath,
}

### Image Retrieval
Before downloading the images, check how many images are available for your inputs

In [20]:
inputs

{'polygon': [[[174.05828631293548, -41.557194569175444],
   [174.14867966548945, -41.557194569175444],
   [174.14867966548945, -41.498578245031055],
   [174.05828631293548, -41.498578245031055],
   [174.05828631293548, -41.557194569175444]]],
 'dates': ['1900-01-01', '2030-01-01'],
 'daterange': 'yes',
 'sat_list': ['L5', 'L7', 'L8', 'L9'],
 'sitename': 'nzd0357',
 'filepath': '/mnt/COASTGUARD/Data'}

In [21]:
inputs = Download.check_images_available(inputs)

Images available between 1900-01-01 and 2030-01-01:
- In Landsat Tier 1 & Sentinel-2 Level-1C:
  L5: 75 images
  L7: 461 images
  L8: 236 images
  L9: 82 images
  Total: 854 images
- In Landsat Tier 2:
  L5: 8 images
  L7: 20 images
  L8: 8 images
  L9: 1 images
  Total: 37 images


In [22]:
inputs

{'polygon': [[[174.05828631293548, -41.557194569175444],
   [174.14867966548945, -41.557194569175444],
   [174.14867966548945, -41.498578245031055],
   [174.05828631293548, -41.498578245031055],
   [174.05828631293548, -41.557194569175444]]],
 'dates': ['1900-01-01', '2030-01-01'],
 'daterange': 'yes',
 'sat_list': ['L5', 'L7', 'L8', 'L9'],
 'sitename': 'nzd0357',
 'filepath': '/mnt/COASTGUARD/Data'}

### Image Download
Compile the metadata from the Google Earth Engine server

In [19]:
metadata

{'L5': {'filenames': ['LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030721',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030806',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030822',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031009',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031126',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031212',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031228',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040214',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040301',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040317',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040402',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040418',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040504',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040520',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040605',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040621',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040707',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040723',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040808',
   'LANDSAT/

In [15]:
Sat = Download.RetrieveImages(inputs)
metadata = Download.CollectMetadata(inputs, Sat)

retrieving image metadata...
Metadata already exists and was loaded


In [10]:
metadata

{'L5': {'filenames': ['LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030721',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030806',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030822',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031009',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031126',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031212',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031228',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040214',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040301',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040317',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040402',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040418',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040504',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040520',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040605',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040621',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040707',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040723',
   'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040808',
   'LANDSAT/

### <font color='red'>Vegetation Edge Settings</font>
ONLY EDIT THESE IF ADJUSTMENTS ARE NEEDED; for example, if you are getting no/disjointed edges, or  if you want to adjust the threshold used for detection in each image.

In [11]:
BasePath = "test/" + sitename + "/lines"

os.makedirs(BasePath, exist_ok=True)

projection_epsg, _ = Toolbox.FindUTM(polygon[0][0][1], polygon[0][0][0])
print(projection_epsg)
projection_epsg = 2193

settings = {
    # general parameters:
    "cloud_thresh": cloud_thresh,  # threshold on maximum cloud cover
    "output_epsg": projection_epsg,  # epsg code of spatial reference system desired for the output
    "wetdry": wetdry,  # extract wet-dry boundary as well as veg
    # quality control:
    "check_detection": True,  # if True, shows each shoreline detection to the user for validation
    "adjust_detection": False,  # if True, allows user to adjust the postion of each shoreline by changing the threhold
    "save_figure": True,  # if True, saves a figure showing the mapped shoreline for each image
    # [ONLY FOR ADVANCED USERS] shoreline detection parameters:
    "min_beach_area": 200,  # minimum area (in metres^2) for an object to be labelled as a beach
    "buffer_size": 250,  # radius (in metres) for buffer around sandy pixels considered in the shoreline detection
    "min_length_sl": 100,  # minimum length (in metres) of shoreline perimeter to be valid
    "cloud_mask_issue": False,  # switch this parameter to True if sand pixels are masked (in black) on many images
    # add the inputs defined previously
    "inputs": inputs,
    "projection_epsg": projection_epsg,
    "year_list": years,
}
settings

32760


{'cloud_thresh': 0.5,
 'output_epsg': 2193,
 'wetdry': False,
 'check_detection': True,
 'adjust_detection': False,
 'save_figure': True,
 'min_beach_area': 200,
 'buffer_size': 250,
 'min_length_sl': 100,
 'cloud_mask_issue': False,
 'inputs': {'polygon': [[[174.05828631293548, -41.557194569175444],
    [174.14867966548945, -41.557194569175444],
    [174.14867966548945, -41.498578245031055],
    [174.05828631293548, -41.498578245031055],
    [174.05828631293548, -41.557194569175444]]],
  'dates': ['2010-01-01', '2010-02-01'],
  'daterange': 'yes',
  'sat_list': ['L5', 'L7'],
  'sitename': 'nzd0357',
  'filepath': '/mnt/COASTGUARD/Data'},
 'projection_epsg': 2193,
 'year_list': [2010]}

### <font color='red'>Tidal Information</font>
Compute tides from FES2014 or FES2022 data which is downloaded from the pyFES server. Only relevant for shoreline processing (as it is used to correct for the effects of tides on the cross-shore waterline position). 

(ONLY RUN IF YOU HAVE `pyfes` INSTALLED AND WANT TIDAL INFO SAVED. If you do, change `tidepath` to the path to your `aviso-fes` folder, see the README for details)

Note: FES2022 is more accurate than FES2014 but takes several minutes longer to compute.

In [ ]:
if wetdry is True:
    tidepath = "../aviso-fes/data/fes2014"
    tideoutpath = os.path.join(
        settings["inputs"]["filepath"],
        "tides",
        settings["inputs"]["sitename"]
        + "_tides_"
        + settings["inputs"]["dates"][0]
        + "_"
        + settings["inputs"]["dates"][1]
        + ".csv",
    )
    daterange = dates
    tidelatlon = [
        (latmin + latmax) / 2,
        (lonmin + lonmax) / 2,
    ]  # centre of bounding box
    Toolbox.ComputeTides(settings, tidepath, tideoutpath, daterange, tidelatlon)

### Vegetation Edge Reference Line Load-In
Read in a shapefile representing the rough edge of vegetation that you want to investigate along. Does not neet to be accurate as it is used to create a coastal buffer for constraining the edge extraction.

In [12]:
referenceLinePath = os.path.join(inputs["filepath"], "referenceLines", referenceLineShp)
referenceLine, ref_epsg = Toolbox.ProcessRefline(referenceLinePath, settings)

settings["reference_shoreline"] = referenceLine
settings["ref_epsg"] = ref_epsg
# Distance to buffer reference line by (this is in metres)
settings["max_dist_ref"] = max_dist_ref
settings["reference_coreg_im"] = (
    None  # leave as None if no coregistration is to be performed
)

In [33]:
gpd.read_file("/mnt/COASTGUARD/Data/referenceLines/nzd0357.geojson").explore(tiles="Esri.WorldImagery")

### <font color='red'>Reference Image for Coregistration</font>
You can now coregister your satellite images using AROSICS. If you want to try coregistering your images to improve timeseries accuracy, <font color='red'>provide a filepath to a reference RGB image.</font>

### Vegetation Line Extraction
**OPTION 1**: Run the extraction tool and return output veg edges as a dictionary of lines with associated image info attached.


In [22]:
filepath, metadata, settings, polygon, dates

('/mnt/COASTGUARD/Data',
 {'L5': {'filenames': ['LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030721',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030806',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20030822',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031009',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031126',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031212',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20031228',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040214',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040301',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040317',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040402',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040418',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040504',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040520',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040605',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040621',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040707',
    'LANDSAT/LT05/C02/T1_TOA/LT05_073089_20040723',
    'LANDSAT/LT05/C0

In [25]:
settings

{'cloud_thresh': 0.5,
 'output_epsg': 2193,
 'wetdry': False,
 'check_detection': True,
 'adjust_detection': False,
 'save_figure': True,
 'min_beach_area': 200,
 'buffer_size': 250,
 'min_length_sl': 100,
 'cloud_mask_issue': False,
 'inputs': {'polygon': [[[174.05828631293548, -41.557194569175444],
    [174.14867966548945, -41.557194569175444],
    [174.14867966548945, -41.498578245031055],
    [174.05828631293548, -41.498578245031055],
    [174.05828631293548, -41.557194569175444]]],
  'dates': ['2010-01-01', '2010-02-01'],
  'daterange': 'yes',
  'sat_list': ['L5', 'L7'],
  'sitename': 'nzd0357',
  'filepath': '/mnt/COASTGUARD/Data'},
 'projection_epsg': 2193,
 'year_list': [2010],
 'reference_shoreline': array([[5405141.54963608, 1688733.79531403,       0.        ],
        [5405131.94965576, 1688736.59538151,       0.        ],
        [5405122.34967545, 1688739.39544899,       0.        ],
        ...,
        [5398965.15301241, 1695374.32651413,       0.        ],
        [5398

In [23]:
!rm "test/{sitename}/{sitename}_output.pkl"
output, output_latlon, output_proj = VegetationLine.extract_veglines(
    metadata, settings, polygon, dates
)

rm: cannot remove 'test/nzd0357/nzd0357_output.pkl': No such file or directory
Already found outputs for L5, L7, L8, L9


In [24]:
import os
import glob
import pickle
import warnings

warnings.filterwarnings("ignore")
import matplotlib

# matplotlib.use('Qt5Agg')
import matplotlib.pyplot as plt

# plt.ion()
from datetime import datetime
from Toolshed import (
    Download,
    Toolbox,
    VegetationLine,
    Plotting,
    PlottingSeaborn,
    Transects,
)
import ee
import geopandas as gpd

sitename = "nzd0151"

dates = ["2010-01-01", "2010-02-01"]
sat_list = ["L5", "L7", "L8", "L9"]

cloud_thresh = 0.5
wetdry = False
referenceLineShp = sitename + ".geojson"
max_dist_ref = 200

filepath = Toolbox.CreateFileStructure(sitename, sat_list)

# Return AOI from reference line bounding box and save AOI folium map HTML in sitename directory
referenceLinePath = os.path.join(filepath, "referenceLines", referenceLineShp)
referenceLineDF = gpd.read_file(referenceLinePath)
polygon, point, lonmin, lonmax, latmin, latmax = Toolbox.AOIfromLine(
    referenceLinePath, max_dist_ref, sitename
)

# It's recommended to convert the polygon to the smallest rectangle (sides parallel to coordinate axes)
polygon = Toolbox.smallest_rectangle(polygon)


# %% Compile Input Settings for Imagery

if len(dates) > 2:
    daterange = "no"
else:
    daterange = "yes"
years = list(
    Toolbox.daterange(
        datetime.strptime(dates[0], "%Y-%m-%d"),
        datetime.strptime(dates[-1], "%Y-%m-%d"),
    )
)

# Put all the inputs into a dictionary
inputs = {
    "polygon": polygon,
    "dates": dates,
    "daterange": daterange,
    "sat_list": sat_list,
    "sitename": sitename,
    "filepath": filepath,
}


# %% Image Retrieval

# Before downloading the images, check how many images are available for your inputs
inputs = Download.check_images_available(inputs)


# %% Image Download

# If you want to include Landsat 7 but DON'T want to include Scan Line Corrector affected images, set SLC=False
Sat = Download.RetrieveImages(inputs, SLC=False)
metadata = Download.CollectMetadata(inputs, Sat)


# %% Vegetation Edge Settings
# ONLY EDIT IF ADJUSTMENTS ARE NEEDED

LinesPath = "Data/" + sitename + "/lines"

if os.path.isdir(LinesPath) is False:
    os.mkdir(LinesPath)

projection_epsg, _ = Toolbox.FindUTM(polygon[0][0][1], polygon[0][0][0])

settings = {
    # general parameters:
    "cloud_thresh": cloud_thresh,  # threshold on maximum cloud cover
    "output_epsg": projection_epsg,  # epsg code of spatial reference system desired for the output
    "wetdry": wetdry,  # extract wet-dry boundary as well as veg
    # quality control:
    "check_detection": False,  # if True, shows each shoreline detection to the user for validation
    "adjust_detection": False,  # if True, allows user to adjust the postion of each shoreline by changing the threhold
    "save_figure": True,  # if True, saves a figure showing the mapped shoreline for each image
    # [ONLY FOR ADVANCED USERS] shoreline detection parameters:
    "min_beach_area": 200,  # minimum area (in metres^2) for an object to be labelled as a beach
    "buffer_size": 250,  # radius (in metres) for buffer around sandy pixels considered in the shoreline detection
    "min_length_sl": 500,  # minimum length (in metres) of shoreline perimeter to be valid
    "cloud_mask_issue": False,  # switch this parameter to True if sand pixels are masked (in black) on many images
    # add the inputs defined previously
    "inputs": inputs,
    "projection_epsg": projection_epsg,
    "year_list": years,
}

referenceLine, ref_epsg = Toolbox.ProcessRefline(referenceLinePath, settings)

settings["reference_shoreline"] = referenceLine
settings["ref_epsg"] = ref_epsg
# Distance to buffer reference line by (this is in metres)
settings["max_dist_ref"] = max_dist_ref
settings["reference_coreg_im"] = None

output, output_latlon, output_proj = VegetationLine.extract_veglines(
    metadata, settings, polygon, dates
)
print(output)

Images available between 2010-01-01 and 2010-02-01:
- In Landsat Tier 1 & Sentinel-2 Level-1C:
  L5: 5 images
  L7: 6 images
  L8: 0 images
  L9: 0 images
  Total: 11 images
- In Landsat Tier 2:
  L5: 0 images
  L7: 0 images
  L8: 0 images
  L9: 0 images
  Total: 0 images
retrieving image metadata...
Metadata already exists and was loaded
Already found outputs for L5, L7, L8, L9
{'L5': {'dates': ['2003-07-21', '2003-08-06', '2003-09-07', '2003-10-25', '2003-12-12', '2004-02-14', '2004-03-01', '2004-04-02', '2004-04-18', '2004-05-04', '2004-05-20', '2004-06-05', '2004-07-07', '2004-07-23', '2004-08-24', '2004-09-25', '2005-01-15', '2005-02-16', '2005-03-04', '2005-04-21', '2005-05-07', '2005-05-23', '2005-06-08', '2005-07-26', '2005-10-30', '2006-02-03', '2006-02-19', '2006-04-08', '2006-06-27', '2007-09-18', '2008-12-25', '2009-02-11', '2010-01-13', '2010-02-14', '2010-10-28', '2010-11-13', '2010-12-31', '2011-02-17', '2003-07-21', '2003-08-06', '2003-10-25', '2004-02-14', '2004-03-01'

In [ ]:
BasePath = "Data/" + sitename + "/lines"

if os.path.isdir(BasePath) is False:
    os.mkdir(BasePath)

### Vegetation Line Extraction Load-In
**OPTION 2**: Load in pre-existing output file generated from a previous run of the vegetation edge extraction tool.


In [26]:
output, output_latlon, output_proj = Toolbox.ReadOutput(inputs)

# Remove Duplicate Lines
# For images taken on the same date by the same satellite, keep only the longest line
output = Toolbox.RemoveDuplicates(output)

0 duplicates


### Save Veglines as Local Shapefiles
You **DO NOT** need to run this again if you have already exported a previous run to a shapefile, especially not if you have then edited/tidied any unwanted lines for further analysis in an external GIS software (as rerunning this cell will overwrite your edits!).

In [6]:
# Save output veglines
Toolbox.SaveConvShapefiles(output, BasePath, sitename, settings["output_epsg"])
# Save output shorelines if they were generated
if settings["wetdry"] == True:
    Toolbox.SaveConvShapefiles_Water(
        output, BasePath, sitename, settings["output_epsg"]
    )

saving shapefile to Data/nzd0151/lines/nzd0151_2010-01-13_2010-01-29_veglines.shp


### <font color='red'>Define Settings for Cross-shore Transects</font>
Edit me to define the characteristics of the cross-shore transects generated for intersecting with the extracted vegetation edges.

In [7]:
SmoothingWindowSize = 21
NoSmooths = 100
TransectSpacing = 10
DistanceInland = 100
DistanceOffshore = 100

# Provide average beach slope (tanBeta) for site, for calculating corrected beach widths
# Set to 'None' if you want to use CoastSat.slope to calculate per-transect slopes for correcting with
beachslope = None

### Create Cross-shore Transects
Generate transects based on the above settings.

In [14]:
VegBasePath = "Data/" + sitename + "/lines"
VeglineShp = glob(BasePath + "/*veglines.shp")
VeglineGDF = gpd.read_file(VeglineShp[0])
VeglineGDF = VeglineGDF.sort_values(
    by="dates"
)  # sort GDF by dates to ensure transect intersects occur in chronological order
VeglineGDF = VeglineGDF.reset_index(drop=True)  # reset GDF index after date sorting
VeglineGDF

dates            times                                      filename  \
0  2010-01-13  21:56:25.416000  LANDSAT/LT05/C02/T1_TOA/LT05_073085_20100113   
1  2010-01-13  21:56:49.389000  LANDSAT/LT05/C02/T1_TOA/LT05_073086_20100113   
2  2010-01-29  21:56:53.427000  LANDSAT/LT05/C02/T1_TOA/LT05_073086_20100129   

   cloud_cove  idx  vthreshold  wthreshold  tideelev satname  \
0         0.0    0      -0.054         NaN       NaN      L5   
1         0.0    2       0.290         NaN       NaN      L5   
2         0.0    3       0.046         NaN       NaN      L5   

                                            geometry  
0  LINESTRING (298838.719 5938446, 298847 5938432...  
1  LINESTRING (298788.576 5938446, 298793.39 5938...  
2  LINESTRING (298822.774 5938446, 298827.278 593...

### Transect-Veg Intersections
Create (or load existing) a GeoDataFrame holding intersections with veg edges along each transect.

In [13]:
transects = gpd.read_file("../CoastSat/transects.geojson")
transects[transects.site_id == sitename]

id  site_id  orientation   along_dist  along_dist_norm  \
100931  nzd0151-0000  nzd0151    60.304974     0.000000         0.000000   
100932  nzd0151-0001  nzd0151    63.916650    99.739135         0.083175   
100933  nzd0151-0002  nzd0151    67.518892   199.739135         0.166567   
100934  nzd0151-0003  nzd0151    73.350548   299.739135         0.249959   
100935  nzd0151-0004  nzd0151    76.860825   399.522715         0.333171   
100936  nzd0151-0005  nzd0151    72.915709   499.210893         0.416304   
100937  nzd0151-0006  nzd0151    71.311917   599.210893         0.499696   
100938  nzd0151-0007  nzd0151    71.311917   699.210893         0.583088   
100939  nzd0151-0008  nzd0151    71.311917   799.210893         0.666481   
100940  nzd0151-0009  nzd0151    68.928291   899.210893         0.749873   
100941  nzd0151-0010  nzd0151    65.683933   999.151116         0.833215   
100942  nzd0151-0011  nzd0151    64.825142  1099.151116         0.916608   
100943  nzd0151-0012  nzd0151    64.825142  1199.151116         1.000000   

        beach_slope     cil     ciu     trend  n_points  n_points_nonan  \
100931        0.015  0.0149  0.0151 -0.505212     536.0           213.0   
100932        0.020  0.0199  0.0208 -0.442817     536.0           283.0   
100933        0.025  0.0249  0.0258 -0.310107     536.0           295.0   
100934        0.030  0.0289  0.0304 -0.209078     536.0           306.0   
100935        0.030  0.0296  0.0304 -0.241800     536.0           317.0   
100936        0.030  0.0297  0.0302 -0.258714     536.0           327.0   
100937        0.030  0.0299  0.0303 -0.173519     536.0           313.0   
100938        0.030  0.0297  0.0303  0.017817     536.0           328.0   
100939        0.030  0.0297  0.0302 -0.008635     536.0           339.0   
100940        0.030  0.0299  0.0347  0.153431     536.0           337.0   
100941        0.030  0.0299  0.0349  0.011661     536.0           342.0   
100942        0.030  0.0298  0.0307 -0.049313     536.0           337.0   
100943        0.025  0.0249  0.0257 -0.152546     536.0           321.0   

                                                 geometry  
100931  LINESTRING (174.74715 -36.68087, 174.75027 -36...  
100932  LINESTRING (174.74754 -36.68141, 174.75077 -36...  
100933  LINESTRING (174.74784 -36.682, 174.75116 -36.6...  
100934  LINESTRING (174.74812 -36.68252, 174.75156 -36...  
100935  LINESTRING (174.74826 -36.68314, 174.75176 -36...  
100936  LINESTRING (174.74853 -36.68393, 174.75197 -36...  
100937  LINESTRING (174.74884 -36.68465, 174.75224 -36...  
100938  LINESTRING (174.74912 -36.68534, 174.75253 -36...  
100939  LINESTRING (174.74941 -36.68602, 174.75281 -36...  
100940  LINESTRING (174.74972 -36.68676, 174.75308 -36...  
100941  LINESTRING (174.75012 -36.68749, 174.7534 -36....  
100942  LINESTRING (174.75051 -36.68816, 174.75377 -36...  
100943  LINESTRING (174.7509 -36.68882, 174.75415 -36....

In [ ]:
Transects.ProduceTransects(
    settings,
    SmoothingWindowSize,
    NoSmooths,
    TransectSpacing,
    DistanceInland,
    DistanceOffshore,
    VegBasePath,
    referenceLineShp,
)

Reference shoreline is correctly oriented

Coast: Initialising Coast object
Coast.ReadCoastShp: Read Coastline, no of coast segments is 1
	Coastline    1 /    1
Coast: Smoothing CoastLines
Coast.WriteCoastShp: Writing coast line to a shapefile
Coast.GenerateTransectNormals: Generating CoastLine transects perpendicular to the coast
Coast.WriteSimpleTransectsShp: Writing coastal transects and attributes to a shapefile


LineID  TransectID                                           geometry  \
0         0           0  LINESTRING (298926.643 5938294.737, 298761.363...   
1         0           1  LINESTRING (298932.583 5938285.976, 298766.648...   
2         0           2  LINESTRING (298938.868 5938276.554, 298771.467...   
3         0           3  LINESTRING (298944.954 5938267.128, 298776.23 ...   
4         0           4  LINESTRING (298951.981 5938255.511, 298779.524...   
..      ...         ...                                                ...   
96        0          96  LINESTRING (299294.907 5937394.738, 299113.749...   
97        0          97  LINESTRING (299299.555 5937384.715, 299117.519...   
98        0          98  LINESTRING (299303.838 5937375.254, 299121.484...   
99        0          99  LINESTRING (299308.092 5937365.732, 299125.388...   
100       0         100  LINESTRING (299312.225 5937356.42, 299129.368 ...   

                         reflinepnt  
0     POINT (298844.41 5938238.706)  
1    POINT (298850.468 5938230.726)  
2    POINT (298855.773 5938222.231)  
3    POINT (298860.666 5938213.481)  
4     POINT (298865.549 5938204.75)  
..                              ...  
96   POINT (299204.514 5937352.451)  
97   POINT (299208.716 5937343.375)  
98   POINT (299212.746 5937334.222)  
99   POINT (299216.776 5937325.069)  
100  POINT (299220.806 5937315.917)  

[101 rows x 4 columns]

In [30]:
TransectGDF = transects[transects.site_id == sitename]
TransectGDF["reflinepnt"] = transects.geometry.centroid
TransectGDF.rename(columns={"id": "TransectID"}, inplace=True)
display(TransectGDF)
TransectGDF = TransectGDF[["site_id", "TransectID", "geometry", "reflinepnt"]]
next(TransectGDF.itertuples())

TransectID  site_id  orientation   along_dist  along_dist_norm  \
100931  nzd0151-0000  nzd0151    60.304974     0.000000         0.000000   
100932  nzd0151-0001  nzd0151    63.916650    99.739135         0.083175   
100933  nzd0151-0002  nzd0151    67.518892   199.739135         0.166567   
100934  nzd0151-0003  nzd0151    73.350548   299.739135         0.249959   
100935  nzd0151-0004  nzd0151    76.860825   399.522715         0.333171   
100936  nzd0151-0005  nzd0151    72.915709   499.210893         0.416304   
100937  nzd0151-0006  nzd0151    71.311917   599.210893         0.499696   
100938  nzd0151-0007  nzd0151    71.311917   699.210893         0.583088   
100939  nzd0151-0008  nzd0151    71.311917   799.210893         0.666481   
100940  nzd0151-0009  nzd0151    68.928291   899.210893         0.749873   
100941  nzd0151-0010  nzd0151    65.683933   999.151116         0.833215   
100942  nzd0151-0011  nzd0151    64.825142  1099.151116         0.916608   
100943  nzd0151-0012  nzd0151    64.825142  1199.151116         1.000000   

        beach_slope     cil     ciu     trend  n_points  n_points_nonan  \
100931        0.015  0.0149  0.0151 -0.505212     536.0           213.0   
100932        0.020  0.0199  0.0208 -0.442817     536.0           283.0   
100933        0.025  0.0249  0.0258 -0.310107     536.0           295.0   
100934        0.030  0.0289  0.0304 -0.209078     536.0           306.0   
100935        0.030  0.0296  0.0304 -0.241800     536.0           317.0   
100936        0.030  0.0297  0.0302 -0.258714     536.0           327.0   
100937        0.030  0.0299  0.0303 -0.173519     536.0           313.0   
100938        0.030  0.0297  0.0303  0.017817     536.0           328.0   
100939        0.030  0.0297  0.0302 -0.008635     536.0           339.0   
100940        0.030  0.0299  0.0347  0.153431     536.0           337.0   
100941        0.030  0.0299  0.0349  0.011661     536.0           342.0   
100942        0.030  0.0298  0.0307 -0.049313     536.0           337.0   
100943        0.025  0.0249  0.0257 -0.152546     536.0           321.0   

                                                 geometry  \
100931  LINESTRING (174.74715 -36.68087, 174.75027 -36...   
100932  LINESTRING (174.74754 -36.68141, 174.75077 -36...   
100933  LINESTRING (174.74784 -36.682, 174.75116 -36.6...   
100934  LINESTRING (174.74812 -36.68252, 174.75156 -36...   
100935  LINESTRING (174.74826 -36.68314, 174.75176 -36...   
100936  LINESTRING (174.74853 -36.68393, 174.75197 -36...   
100937  LINESTRING (174.74884 -36.68465, 174.75224 -36...   
100938  LINESTRING (174.74912 -36.68534, 174.75253 -36...   
100939  LINESTRING (174.74941 -36.68602, 174.75281 -36...   
100940  LINESTRING (174.74972 -36.68676, 174.75308 -36...   
100941  LINESTRING (174.75012 -36.68749, 174.7534 -36....   
100942  LINESTRING (174.75051 -36.68816, 174.75377 -36...   
100943  LINESTRING (174.7509 -36.68882, 174.75415 -36....   

                         reflinepnt  
100931  POINT (174.74871 -36.68015)  
100932  POINT (174.74916 -36.68078)  
100933   POINT (174.7495 -36.68144)  
100934  POINT (174.74984 -36.68211)  
100935  POINT (174.75001 -36.68282)  
100936  POINT (174.75025 -36.68351)  
100937  POINT (174.75054 -36.68419)  
100938  POINT (174.75082 -36.68487)  
100939  POINT (174.75111 -36.68556)  
100940   POINT (174.7514 -36.68624)  
100941   POINT (174.75176 -36.6869)  
100942  POINT (174.75214 -36.68755)  
100943   POINT (174.75252 -36.6882)

Pandas(Index=100931, site_id='nzd0151', TransectID='nzd0151-0000', geometry=<LINESTRING (174.747 -36.681, 174.75 -36.679)>, reflinepnt=<POINT (174.749 -36.68)>)

In [35]:
VeglineGDF

dates            times                                      filename  \
0  2010-01-13  21:56:25.416000  LANDSAT/LT05/C02/T1_TOA/LT05_073085_20100113   
1  2010-01-13  21:56:49.389000  LANDSAT/LT05/C02/T1_TOA/LT05_073086_20100113   
2  2010-01-29  21:56:53.427000  LANDSAT/LT05/C02/T1_TOA/LT05_073086_20100129   

   cloud_cove  idx  vthreshold  wthreshold  tideelev satname  \
0         0.0    0      -0.054         NaN       NaN      L5   
1         0.0    2       0.290         NaN       NaN      L5   
2         0.0    3       0.046         NaN       NaN      L5   

                                            geometry  
0  LINESTRING (298838.719 5938446, 298847 5938432...  
1  LINESTRING (298788.576 5938446, 298793.39 5938...  
2  LINESTRING (298822.774 5938446, 298827.278 593...

In [33]:
m = VeglineGDF.explore()
TransectGDF.explore(m=m, color="red", name="transects")

In [ ]:
TransectInterGDF = Transects.GetIntersections(BasePath, TransectGDF, VeglineGDF)
dt_lookup = {}
for _, row in TransectInterGDF.iterrows():
    for i in range(len(row.dates)):
        dt = row.dates[i] + " " + row.times[i]
        if dt not in dt_lookup:
            dt_lookup[dt] = {"dates": dt, "satname": row.satname[i]}
        dt_lookup[dt][row.TransectID] = row.distances[i]
import pandas as pd

df = pd.DataFrame(dt_lookup.values())
fn = os.path.join(
    settings["inputs"]["filepath"],
    settings["inputs"]["sitename"],
    "transect_time_series.csv",
)
df.to_csv(fn, index=False, float_format="%.2f")

performing intersections between transects...
formatting into GeoDataFrame...
TransectDict with intersections created.


### Transect-Water Intersections
Create (or load existing) a GeoDataFrame holding intersections with waterlines along each transect. 

In [ ]:
if os.path.isfile(
    os.path.join(
        filepath, sitename, "intersections", sitename + "_transect_water_intersects.pkl"
    )
):
    print("Transect Intersect + Water GDF exists and was loaded")
    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_water_intersects.pkl",
        ),
        "rb",
    ) as f:
        TransectInterGDFWater = pickle.load(f)
else:
    if settings["wetdry"] == True:
        TransectInterGDFWater = Transects.GetWaterIntersections(
            BasePath, TransectGDF, TransectInterGDF, WaterlineGDF, settings, output
        )

    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_water_intersects.pkl",
        ),
        "wb",
    ) as f:
        pickle.dump(TransectInterGDFWater, f)

### Transect-Waves Intersections
Create (or load existing) a GeoDataFrame holding intersections with topographic data along each transect. This is for comparing veg edge positions with nearshore wave conditions at the time the image was taken. NOTE: this requires you to have a Copernicus Marine Service (CMEMS) account with access to their hindcast model, as you will be asked for a username and password. This should also be run before the tidal corrections and beach with steps if you want to include runup in your corrections.

In [ ]:
if os.path.isfile(
    os.path.join(
        filepath, sitename, "intersections", sitename + "_transect_wave_intersects.pkl"
    )
):
    print("Transect Intersect + Wave GDF exists and was loaded")
    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_wave_intersects.pkl",
        ),
        "rb",
    ) as f:
        TransectInterGDFWave = pickle.load(f)
else:
    TransectInterGDFWave = Transects.WavesIntersect(
        settings, TransectInterGDF, BasePath, output, lonmin, lonmax, latmin, latmax
    )

    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_wave_intersects.pkl",
        ),
        "wb",
    ) as f:
        pickle.dump(TransectInterGDFWave, f)

### Additional wave-based WL metrics
This is for comparing shoreline change with vegetation change, and for quantifying the beach width between the two for each image. If you would like to include runup in your waterline corrections, add `TransectInterGDFWave` to `GetWaterIntersections()`:

```TransectInterGDFWater = Transects.GetWaterIntersections(BasePath, TransectGDF, TransectInterGDF, WaterlineGDF, settings, output, TransectInterGDFWave, beachslope)```

If you want to include runup AND calculate slopes using CoastSat.slope (recommended), exclude the `beachslope` variable:

`TransectInterGDFWater = Transects.GetWaterIntersections(BasePath, TransectGDF, TransectInterGDF, WaterlineGDF, settings, output, TransectInterGDFWave)`

In [ ]:
if "wlcorrdist" not in TransectInterGDFWater.columns:
    # Tidal correction to get corrected distances along transects
    TransectInterGDFWater = Transects.WLCorrections(
        settings, output, TransectInterGDFWater, TransectInterGDFWave
    )
    # Calculate width between VE and corrected WL
    TransectInterGDFWater = Transects.CalcBeachWidth(
        settings, TransectGDF, TransectInterGDFWater
    )
    # Calculate rates of change on corrected WL and save as Transects shapefile
    TransectInterGDFWater = Transects.SaveWaterIntersections(
        TransectInterGDFWater, WaterlineGDF, BasePath, sitename
    )
    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_water_intersects.pkl",
        ),
        "wb",
    ) as f:
        pickle.dump(TransectInterGDFWater, f)

### Transect-Topo Intersections
Create (or load existing) a GeoDataFrame holding intersections with topographic data along each transect. This is for comparing veg edge positions with dune slopes. <font color='red'>Edit the TIF filename</font> if you want to run this intersection process.

In [ ]:
# EDIT ME: Path to slope raster for extracting slope values
TIF = "/path/to/Slope_Raster.tif"

if os.path.isfile(
    os.path.join(
        filepath, sitename, "intersections", sitename + "_transect_topo_intersects.pkl"
    )
):
    print("Transect Intersect + Topo GDF exists and was loaded")
    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_topo_intersects.pkl",
        ),
        "rb",
    ) as f:
        TransectInterGDFTopo = pickle.load(f)
else:
    # Update Transects with Transition Zone widths and slope if available
    TransectInterGDFTopo = Transects.TZIntersect(
        settings, TransectInterGDF, VeglineGDF, BasePath
    )
    TransectInterGDFTopo = Transects.SlopeIntersect(
        settings, TransectInterGDFTopo, VeglineGDF, BasePath, TIF
    )

    with open(
        os.path.join(
            filepath,
            sitename,
            "intersections",
            sitename + "_transect_topo_intersects.pkl",
        ),
        "wb",
    ) as f:
        pickle.dump(TransectInterGDFTopo, f)

### <font color='red'>Plotting</font>
Edit the desired Transect IDs to plot timeseries of veg change and beach width change across 

In [ ]:
# Timeseries Plotting

# EDIT ME: Select transect ID to plot
# You can plot subplots within a list of plot IDs, e.g. [[sub1, sub2], plot2]
# You can also comment Line 1 out and uncomment Line 2 to create plots for ALL Transect IDs
# NOTE: If you want to plot ALL transects, it's recommended you switch ShowPlot=False

# TransectIDs = [[25, 30, 35], 50, 75]  # Line 1
TransectIDs = list(TransectInterGDF["TransectID"])  # Line 2

for TransectID in TransectIDs:
    # Plot timeseries of cross-shore veg position
    Plotting.VegTimeseries(
        sitename, TransectInterGDF, TransectID, Hemisphere="S", ShowPlot=True
    )
    # If plotting veg and water lines together
    if settings["wetdry"]:
        Plotting.VegWaterTimeseries(
            sitename, TransectInterGDFWater, TransectID, Hemisphere="S", ShowPlot=True
        )

TypeError: Cannot index by location index with a non-integer key

In [ ]:
# Beach Width Plotting

# Select transect ID to plot
TransectIDs = [[25, 30, 35], 50, 75]
for TransectID in TransectIDs:
    # Plot timeseries of cross-shore width between water edge and veg edge
    Plotting.WidthTimeseries(
        sitename, TransectInterGDFWater, TransectID, Hemisphere="N"
    )

## OPTIONAL: Validation
### <font color='red'>Validation Settings</font>
Most likely you won't need to validate your lines, but if you do, edit these parameters.

In [ ]:
# Name of date column in validation edges shapefile (case sensitive!)
DatesCol = "Date"
ValidationShp = "./Validation/StAndrews_Veg_Edge_combined_2007_2022_singlepart.shp"
# EDIT ME: List of transect ID tuples (startID, finishID)
TransectIDList = [(595, 711), (726, 889), (972, 1140), (1141, 1297)]

In [ ]:
# Satellite Edges Validation
validpath = os.path.join(os.getcwd(), "Data", sitename, "validation")

if os.path.isfile(os.path.join(validpath, sitename + "_valid_intersects.pkl")):
    print("ValidDict exists and was loaded")
    with open(os.path.join(validpath, sitename + "_valid_intersects.pkl"), "rb") as f:
        ValidInterGDF = pickle.load(f)
else:
    ValidInterGDF = Transects.ValidateSatIntersects(
        sitename, ValidationShp, DatesCol, TransectGDF, TransectInterGDF
    )
    with open(os.path.join(validpath, sitename + "_valid_intersects.pkl"), "wb") as f:
        pickle.dump(ValidInterGDF, f)


# Quantify errors between validation and satellite derived lines
for TransectIDs in TransectIDList:
    Toolbox.QuantifyErrors(sitename, VeglineGDF, "dates", ValidInterGDF, TransectIDs)

### <font color='red'>Validation Plots</font>
Plot violin plots, probability density functions and regression lines of the cross-shore distance along each transect between each satellite-derived veg edge and validation veg edge.

In [ ]:
# EDIT ME: List of transect ID tuples (startID, finishID)
TransectIDList = [(0, 1741)]

for TransectIDs in TransectIDList:
    PlotTitle = (
        "Accuracy of Transects " + str(TransectIDs[0]) + " to " + str(TransectIDs[1])
    )
    PlottingSeaborn.SatViolin(
        sitename, VeglineGDF, "dates", ValidInterGDF, TransectIDs, PlotTitle
    )
    PlottingSeaborn.SatPDF(
        sitename, VeglineGDF, "dates", ValidInterGDF, TransectIDs, PlotTitle
    )
    Plotting.SatRegress(
        sitename, VeglineGDF, "dates", ValidInterGDF, TransectIDs, PlotTitle
    )